In [ ]:
# There are two standard ways to do linear programming in python:
# cvxopt and scipy.
# We use scipy, which has a cleaner API, even though it's usually a bit slower.

# pip install scipy
import scipy.optimize
# https://docs.scipy.org/doc/scipy/reference/optimize.html

import numpy as np

Problem 1: a balanced diet
-------------------

Given the nutrition information and cost of a bunch of foods, and your nutrition requirements, find the cheapest collection of food to eat.

In [ ]:
def parse_csv(s):
    """Utility function to parse a CSV into a list of dictionaries.
    
    Assumes all columns after the first are numeric, and parses into floats.
    """
    lines = s.splitlines()
    columns = [x.strip() for x in lines[0].split(',')]
    
    answer = []
    for row in lines[1:]:
        fields = row.split(',')
        d = {}
        d[columns[0]] = fields[0]
        for name, value in zip(columns[1:], fields[1:]):
            d[name] = float(value)
        answer.append(d)
    return answer


# A random selection of foods you are interested in eating
foods = parse_csv("""
name,            calories, fat, carbs, protein,  cost, sodium
doritos (bag),        150,   8,    17,       2,  0.99,    180
soylent (bottle),     400,  21,    36,      20,  3.25,    300
bok choy (cup),       100, 1.5,    15,    13.5,  1.85,     58
hummus (cup),         409,  24,    35,      19,  2.22,    932
pizza (slice),        304,  11,    38,      13,  2.00,    640
chicken (1/2 lb),     372,   8,     0,      70,  1.60,    165
""".strip())


# Dietary recommendations vary by gender/age/weight/activity level.
#  https://fnic.nal.usda.gov/fnic/dri-calculator/index.php
# This is for a 20-year-old sedentary 150-lb 5'9" man.

nutrients = parse_csv("""
name,      min,   max
calories, 2400, 2600
fat,        56,    97
carbs,     281,   406
protein,    55,   999
sodium,   1500,  2300
""".strip())

# Fun fact: I initially didn't include sodium as a nutrient.  The recommended diet was almost entirely pizza.

In [ ]:
# This is the format:
print(foods[0])
print(nutrients)

In [ ]:
# Let's find the cheapest collection of food that satisfies our nutrition requirements

def solve(foods, nutrients):
    # First, produce the linear program.
    
    # One variable per food
    # two constraints per nutrient
    A = []
    b = []
    for nutrient in nutrients:
        name = nutrient['name']
        row = np.array([food[name] for food in foods])

        A.append(-row)                # Lower bound
        b.append(-nutrient['min'])

        A.append(row)                 # Upper bound
        b.append(nutrient['max'])


    c = [food['cost'] for food in foods]
    A, b, c = map(np.array, (A, b, c))

    
    # Now, optimize it.
    # You might wonder how I chose the options in the below calls. If you run without those options,
    # it gives an error/warning and suggests setting them.

    result = scipy.optimize.linprog(c, A, b, method='simplex', options={'tol':1e-8})
    #result = scipy.optimize.linprog(c, A, b, method='interior-point', options={'lstsq': True})

    print(result)
    print()

    
    print('Components of a "balanced" diet:')
    for food, val in zip(foods, result['x']):
        print(f"{food['name'].rjust(20)}    {val:0.2f}")

    print()
    print('Resulting nutrition:', A[1::2].dot(result['x']))
    print()
    print("Cost of diet:", c.dot(result['x']))
              
    # Problem 1.b : compute dual variables here.
    #### YOUR CODE:
    # Compute dual variables
    # Print dual variables
    # Print dual value
    ####  

              
solve(foods, nutrients)
# Note: nutrition is complicated. Actually following this diet is not recommended.

Problem 1.a
---------------

Try switching the optimization above from `method='simplex'` to `method='interior-point'`.  The `Resulting nutrition` line will change a bit.  Why?

Problem 1.b
-----------------

Consider the dual linear program.  How many variables are there?  What do they represent?  Can you predict which dual variables will be zero?

Now modify the above linear program to also compute and output the dual variables.  Hint: to compute the result, just call `scipy.optimize.linprog` after reordering, transposing, and/or flipping the signs of the variables `A, b, c`.  The objective value should be the same (but maybe with a different sign).

What are the largest dual variables in your solution, and what do they represent?

Problem 1.c
-----------------
Suppose that you believe the story here:

https://www.npr.org/sections/thetwo-way/2016/09/13/493739074/50-years-ago-sugar-industry-quietly-paid-scientists-to-point-blame-at-fat
http://time.com/4130043/lobbying-politics-dietary-guidelines/

that the sugar lobby has gotten the government to require too much carbs, and be too restrictive on fat.  Is that consistent with your observations in part (b)?


How much would the cost of the diet change if you allowed yourself 5g more fat per day?  How about 5g less carbs per day?

First, try to make a prediction using your dual variables.  Then compute the actual value, as below.  If you didn't predict it correctly beforehand, figure out how you should have predicted it.

Would the same prediction method work if you allowed 1000g more fat per day?  If not, why not?

In [ ]:
new_nutrients = parse_csv("""
YOUR CODE HERE
""".strip())

solve(foods, new_nutrients)

Problem 1.d
-----------------

Now compute _your_ "optimal" diet.  Find the nutrition information of foods you eat, and choose daily nutrition goals for yourself.  Give yourself a daily budget, and assign a "tastiness" to each food.

What is the maximally tasty selection of food that fits into your budget and satisfies your nutritional requirements?